In [134]:
import matplotlib.pyplot as plt
import numpy as np
import random
from PIL import Image
from torch.utils.data import Dataset, DataLoader
from torch import nn
import os
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
tpr = torch.hub.load('yangsenius/TransPose:main', 'tpr_a4_256x192', pretrained=True)
#tph = torch.hub.load('yangsenius/TransPose:main', 'tph_a4_256x192', pretrained=True, device=device)


#print(tph)
DATASET_PATH = './dataset/'
positions = os.listdir(DATASET_PATH)
#print(os.listdir(DATASET_PATH+entries[0]))
images = list()

def add_margin(pil_img, top, right, bottom, left, color):
    width, height = pil_img.size
    new_width = width + right + left
    new_height = height + top + bottom
    result = Image.new(pil_img.mode, (new_width, new_height), color)
    result.paste(pil_img, (left, top))
    return result

class YogaPoseDataset(Dataset):

    def __init__(self, dataset_path):
        self.data_path = dataset_path
        # call to init the data
        self.size = 256,192
        self._init_data()

    def _init_data(self):
        positions = os.listdir(self.data_path)
        images = list()
        labels = list()
        for idx, position in enumerate(positions):
            for file in os.listdir(DATASET_PATH + position):
                with Image.open(DATASET_PATH + position + '/' + file, "r") as f:
                    # f.show()
                    #print("EFFE",f,type(f))
                    f = f.convert("L")
                    pixels = list(f.getdata())
                    #print(f.size)
                    f.thumbnail(self.size)
                    pixels = list(f.getdata())
                    width, height = f.size
                    #print(f.size)
                    f = add_margin(f,192-height,256-width,0,0,color=0)
                    #f.show()
                    #print(f.size)
                    width, height = f.size
                    pixels = [pixels[i * width:(i + 1) * width] for i in range(height)]
                    #print(len(pixels))
                    data = torch.reshape(torch.FloatTensor([f.getdata()]).to(device),(width,height))

                    #print(f.getdata())
                    #print(data.size(),data)
                    images.append(data)

                    labels.append(torch.tensor(idx))

                    # print(data)


        #print(images)
        images = torch.cat(images)
        labels = torch.stack(labels)
        #print(labels)
        #print(images)
        mask = np.arange(labels.size()[0])
        np.random.shuffle(mask)
        #print(type(images),type(images[0]))
        self.images = images[mask]
        self.labels = labels[mask]

    def __len__(self):
        # returns the number of samples in our dataset
        return len(self.images)

    def __getitem__(self, idx):
        # returns the idx-th sample
        return self.images[idx],self.labels[idx]

>>Load pretrained weights from url: https://github.com/yangsenius/TransPose/releases/download/Hub/tp_r_256x192_enc4_d256_h1024_mh8.pth
Successfully loaded model  (on cpu) with pretrained weights!


Using cache found in /home/michele/.cache/torch/hub/yangsenius_TransPose_main


In [ ]:
dataset = YogaPoseDataset(DATASET_PATH)
split_position = int((len(dataset)/10)*7)
trainset = dataset[:split_position]
testset = dataset[split_position:]
print(trainset)

In [ ]:
class PoseClassifier(nn.Module):
    def __init__(self, n_class, fine_tune, pretrained=True):
        super(PoseClassifier, self).__init__()

        self.tph = torch.hub.load('yangsenius/TransPose:main', 'tph_a4_256x192', pretrained=True, device=device)
        self.fc1 = nn.Linear(1000,1000).to(device)
        self.fc2 = nn.Linear(1000,n_class).to(device)
        self.relu = nn.ReLU()

    def forward(self, x):

        x = x.to(device)
        out = self.tph(x)
        out = self.fc1(out)
        #m = nn.BatchNorm1d(1000,device=device)
        #out = m(out)
        out = self.relu(out)
        out = self.fc2(out)
        # *****END OF YOUR CODE (DO NOT DELETE/MODIFY THIS LINE)*****
        return out


In [54]:
X = np.array(dataset[:,1])
#X = X.astype(float)
X.size()

TypeError: 'int' object is not callable

In [39]:

#X = torch.tensor(X)
m = 0
for idx,image in enumerate(X):
    if len(image) > m:
        print(idx,len(image))
        m = len(image)
m

0 4262


4262

In [53]:
type(X)

array([list([array([[255, 255, 255],
              [255, 254, 248],
              [255, 255, 250],
              ...,
              [255, 255, 255],
              [255, 255, 255],
              [255, 255, 255]], dtype=uint8), array([[255, 255, 255],
              [255, 255, 248],
              [255, 255, 250],
              ...,
              [255, 255, 255],
              [255, 255, 255],
              [255, 255, 255]], dtype=uint8), array([[255, 255, 255],
              [255, 255, 248],
              [255, 255, 250],
              ...,
              [255, 255, 255],
              [255, 255, 255],
              [255, 255, 255]], dtype=uint8), array([[255, 255, 255],
              [255, 255, 250],
              [255, 254, 251],
              ...,
              [255, 255, 255],
              [255, 255, 255],
              [255, 255, 255]], dtype=uint8), array([[255, 255, 255],
              [255, 254, 251],
              [255, 254, 251],
              ...,
              [255, 255, 255],